# Characterize Dark Images #

Author: S. Hauf, Version: 0.1

The following code analyzes a set of dark images taken with the AGIPD detector to deduce detector offsets , noise and bad-pixel maps. All three types of constants are evaluated per-pixel and per-memory cell. Data for the detector's three gain stages needs to be present, separated into separate runs.

The evaluated calibration constants are stored locally and injected in the calibration data base.

**The offset** ($O$) is defined as the median ($M$) of the dark signal ($Ds$) over trains ($t$) for a given pixel ($x,y$) and memory cell ($c$). 

**The noise** $N$ is the standard deviation $\sigma$ of the dark signal.

$$ O_{x,y,c} = M(Ds)_{t} ,\,\,\,\,\,\, N_{x,y,c} = \sigma(Ds)_{t}$$

**The bad pixel** mask is encoded as a bit mask.

**"OFFSET_OUT_OF_THRESHOLD":**

Offset outside of bounds:

$$M(O)_{x,y} - \sigma(O)_{x,y} * \mathrm{thresholds\_offset\_sigma} < O < M(O)_{x,y} + \sigma(O)_{x,y} * \mathrm{thresholds\_offset\_sigma} $$

or offset outside of hard limits

$$ \mathrm{thresholds\_offset\_hard}_\mathrm{low} < O < \mathrm{thresholds\_offset\_hard}_\mathrm{high} $$

**"NOISE_OUT_OF_THRESHOLD":**

Noise outside of bounds:

$$M(N)_{x,y} - \sigma(N)_{x,y} * \mathrm{thresholds\_noise\_sigma} < N < M(N)_{x,y} + \sigma(N)_{x,y} * \mathrm{thresholds\_noise\_sigma} $$

or noise outside of hard limits

$$\mathrm{thresholds\_noise\_hard}_\mathrm{low} < N < \mathrm{thresholds\_noise\_hard}_\mathrm{high} $$

**"OFFSET_NOISE_EVAL_ERROR":**

Offset and Noise both not $nan$ values 

Values: $\mathrm{thresholds\_offset\_sigma}$, $\mathrm{thresholds\_offset\_hard}$, $\mathrm{thresholds\_noise\_sigma}$, $\mathrm{thresholds\_noise\_hard}$ are given as parameters.

In [ ]:
cluster_profile = "noDB" # The ipcluster profile to use
in_folder = "/gpfs/exfel/d/raw/SPB/202030/p900138/" # path to input data, required
out_folder = "/gpfs/exfel/data/scratch/ahmedk/test/AGIPD" # path to output to, required
sequences = [0] # sequence files to evaluate.

run_high = 199 # run number in which high gain data was recorded, required
run_med = 200 # run number in which medium gain data was recorded, required
run_low = 201 # run number in which low gain data was recorded, required

mem_cells = 0 # number of memory cells used, set to 0 to automatically infer
local_output = True # output constants locally
db_output = False # output constants to database
bias_voltage = 300 # detector bias voltage
cal_db_interface = "tcp://max-exfl016:8020" # the database interface to use
cal_db_timeout = 3000000 # timeout on caldb requests"
interlaced = False # assume interlaced data format, for data prior to Dec. 2017
rawversion = 2 # RAW file format version
dont_use_dir_date = False # don't use the dir creation date for determining the creation time

thresholds_offset_sigma = 3. # thresholds in terms of n sigma noise for offset deduced bad pixels
thresholds_offset_hard = [4000, 8500] # thresholds in absolute ADU terms for offset deduced bad pixels

thresholds_noise_sigma = 5. # thresholds in terms of n sigma noise for offset deduced bad pixels
thresholds_noise_hard = [4, 20] # thresholds in absolute ADU terms for offset deduced bad pixels

instrument = "SPB"
high_res_badpix_3d = False # set this to True if you need high-resolution 3d bad pixel plots. Runtime: ~ 1h
modules = [0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15]  # module to run for
acq_rate = 0. # the detector acquisition rate, use 0 to try to auto-determine
gain_setting = 0.1 # the gain setting, use 0.1 to try to auto-determine

h5path_ctrl = '/CONTROL/SPB_IRU_AGIPD1M1/MDL/FPGA_COMP_TEST' # path to control information
karabo_da_control = 'AGIPD1MCTRL00' # karabo DA for control infromation

In [ ]:
# imports and things that do not usually need to be changed
from datetime import datetime
import dateutil.parser
import warnings
warnings.filterwarnings('ignore')
from collections import OrderedDict
import os
import h5py
import numpy as np
import matplotlib
import tabulate

matplotlib.use('agg')
import matplotlib.pyplot as plt
from IPython.display import display, Markdown, Latex
%matplotlib inline

from cal_tools.tools import (gain_map_files, parse_runs, 
                             run_prop_seq_from_path, get_notebook_name, 
                             get_dir_creation_date, save_const_to_h5,
                             get_random_db_interface, get_from_db)
from cal_tools.influx import InfluxLogger
from cal_tools.enums import BadPixels
from cal_tools.plotting import show_overview, plot_badpix_3d, create_constant_overview
from cal_tools.agipdlib import get_gain_setting

# make sure a cluster is running with ipcluster start --n=32, give it a while to start
from ipyparallel import Client

view = Client(profile=cluster_profile)[:]
view.use_dill()

from iCalibrationDB import ConstantMetaData, Constants, Conditions, Detectors, Versions

gains = np.arange(3)

# no need to change this

QUADRANTS = 4
MODULES_PER_QUAD = 4
DET_FILE_INSET = "AGIPD"

IL_MODE = interlaced
max_cells = mem_cells
   
offset_runs = OrderedDict()
offset_runs["high"] = parse_runs(run_high)[0]
offset_runs["med"] = parse_runs(run_med)[0]
offset_runs["low"] = parse_runs(run_low)[0]

creation_time=None
if not dont_use_dir_date:
    creation_time = get_dir_creation_date(in_folder, run_high)


run, prop, seq = run_prop_seq_from_path(in_folder)
logger = InfluxLogger(detector="AGIPD", instrument=instrument, mem_cells=mem_cells,
                      notebook=get_notebook_name(), proposal=prop)

print("Using {} as creation time of constant.".format(creation_time))

cal_db_interface = get_random_db_interface(cal_db_interface)
print('Calibration database interface: {}'.format(cal_db_interface))

loc = None
if instrument == "SPB":
    loc = "SPB_DET_AGIPD1M-1"
    dinstance = "AGIPD1M1"
else:
    loc = "MID_DET_AGIPD1M-1"
    dinstance = "AGIPD1M2"
print("Detector in use is {}".format(loc))    

In [ ]:
control_fname = '{}/r{:04d}/RAW-R{:04d}-{}-S00000.h5'.format(in_folder, run_high, 
                                                             run_high, karabo_da_control)

if gain_setting == 0.1:
    if creation_time.replace(tzinfo=None) < dateutil.parser.parse('2020-01-31'):
        print("Set gain-setting to None for runs taken before 2020-01-31")
        gain_setting = None
    else:
        try:
            gain_setting = get_gain_setting(control_fname, h5path_ctrl)
        except Exception as e:
            print(f'Error while reading gain setting from: \n{control_fname}')
            print(e)
            print("Gain setting is not found in the control information")
            print("Data will not be processed")
            sequences = []

In [ ]:
print("Parameters are:")
print("Proposal: {}".format(prop))
print("Memory cells: {}/{}".format(mem_cells, max_cells))
print("Runs: {}".format([ v for v in offset_runs.values()]))
print("Sequences: {}".format(sequences))
print("Interlaced mode: {}".format(IL_MODE))
print("Using DB: {}".format(db_output))
print("Input: {}".format(in_folder))
print("Output: {}".format(out_folder))
print("Bias voltage: {}V".format(bias_voltage))
print("Gain setting: {}".format(gain_setting))

The following lines will create a queue of files which will the be executed module-parallel. Distiguishing between different gains.

In [ ]:
# set everything up filewise
if not os.path.exists(out_folder):
    os.makedirs(out_folder)

gmf = gain_map_files(in_folder, offset_runs, sequences, DET_FILE_INSET, QUADRANTS, MODULES_PER_QUAD)
gain_mapped_files, total_sequences, total_file_size = gmf

print("Will process at total of {} sequences: {:0.2f} GB of data.".format(total_sequences, total_file_size))

## Calculate Offsets, Noise and Thresholds ##

The calculation is performed per-pixel and per-memory-cell. Offsets are simply the median value for a set of dark data taken at a given gain, noise the standard deviation, and gain-bit values the medians of the gain array.

In [ ]:
import copy
from functools import partial
def characterize_module(il_mode, cells, bp_thresh, rawversion, loc, acq_rate, inp):
    import numpy as np
    import copy
    import h5py
    from cal_tools.enums import BadPixels
    from cal_tools.agipdlib import get_num_cells, get_acq_rate
    
    filename, filename_out, channel = inp
    

    if cells == 0:
        cells = get_num_cells(filename, loc, channel)

    print("Using {} memory cells".format(cells))
    
    if acq_rate == 0.:
        acq_rate = get_acq_rate(filename, loc, channel)
    
    thresholds_offset_hard, thresholds_offset_sigma, thresholds_noise_hard, thresholds_noise_sigma = bp_thresh 

    infile = h5py.File(filename, "r", driver="core")
    if rawversion == 2:
        count = np.squeeze(infile["/INDEX/{}/DET/{}CH0:xtdf/image/count".format(loc, channel)])
        first = np.squeeze(infile["/INDEX/{}/DET/{}CH0:xtdf/image/first".format(loc, channel)])
        last_index = int(first[count != 0][-1]+count[count != 0][-1])
        first_index = int(first[count != 0][0])
    else:
        status = np.squeeze(infile["/INDEX/{}/DET/{}CH0:xtdf/image/status".format(loc, channel)])
        if np.count_nonzero(status != 0) == 0:
            return
        last = np.squeeze(infile["/INDEX/{}/DET/{}CH0:xtdf/image/last".format(loc, channel)])
        first = np.squeeze(infile["/INDEX/{}/DET/{}CH0:xtdf/image/first".format(loc, channel)])
        last_index = int(last[status != 0][-1]) + 1
        first_index = int(first[status != 0][0])
    im = np.array(infile["/INSTRUMENT/{}/DET/{}CH0:xtdf/image/data".format(loc, channel)][first_index:last_index,...])    
    cellIds = np.squeeze(infile["/INSTRUMENT/{}/DET/{}CH0:xtdf/image/cellId".format(loc, channel)][first_index:last_index,...]) 
    
    infile.close()

    if il_mode:
        ga = im[1::2, 0, ...]
        im = im[0::2, 0, ...].astype(np.float32)
        cellIds = cellIds[::2]
    else:
        ga = im[:, 1, ...]
        im = im[:, 0, ...].astype(np.float32)
        
    im = np.rollaxis(im, 2)
    im = np.rollaxis(im, 2, 1)

    ga = np.rollaxis(ga, 2)
    ga = np.rollaxis(ga, 2, 1)

    mcells = cells #max(cells, np.max(cellIds)+1)
    offset = np.zeros((im.shape[0], im.shape[1], mcells))
    gains = np.zeros((im.shape[0], im.shape[1], mcells))
    noise = np.zeros((im.shape[0], im.shape[1], mcells))
    
    for cc in np.unique(cellIds[cellIds < mcells]):
        cellidx = cellIds == cc
        offset[...,cc] = np.median(im[..., cellidx], axis=2)
        noise[...,cc] = np.std(im[..., cellidx], axis=2)
        gains[...,cc] = np.median(ga[..., cellidx], axis=2)
        
    # bad pixels
    bp = np.zeros(offset.shape, np.uint32)
    # offset related bad pixels
    offset_mn = np.nanmedian(offset, axis=(0,1))
    offset_std = np.nanstd(offset, axis=(0,1))    
    
    bp[(offset < offset_mn-thresholds_offset_sigma*offset_std) |
       (offset > offset_mn+thresholds_offset_sigma*offset_std)] |= BadPixels.OFFSET_OUT_OF_THRESHOLD.value
    bp[(offset < thresholds_offset_hard[0]) | (offset > thresholds_offset_hard[1])] |= BadPixels.OFFSET_OUT_OF_THRESHOLD.value
    bp[~np.isfinite(offset)] |= BadPixels.OFFSET_NOISE_EVAL_ERROR.value
    
    # noise related bad pixels
    noise_mn = np.nanmedian(noise, axis=(0,1))
    noise_std = np.nanstd(noise, axis=(0,1))    
    
    bp[(noise < noise_mn-thresholds_noise_sigma*noise_std) |
       (noise > noise_mn+thresholds_noise_sigma*noise_std)] |= BadPixels.NOISE_OUT_OF_THRESHOLD.value
    bp[(noise < thresholds_noise_hard[0]) | (noise > thresholds_noise_hard[1])] |= BadPixels.NOISE_OUT_OF_THRESHOLD.value
    bp[~np.isfinite(noise)] |= BadPixels.OFFSET_NOISE_EVAL_ERROR.value


    return offset, noise, gains, bp, cells, acq_rate
        
        
offset_g = OrderedDict()
noise_g = OrderedDict()
gain_g = OrderedDict()
badpix_g = OrderedDict()
gg = 0

start = datetime.now()
all_cells = []
all_acq_rate = []
for gain, mapped_files in gain_mapped_files.items():
    
    inp = []
    dones = []
    for i in modules:
        qm = "Q{}M{}".format(i//4 +1, i % 4 + 1)    
        if qm in mapped_files and not mapped_files[qm].empty():
            fname_in = mapped_files[qm].get()            
            dones.append(mapped_files[qm].empty())
        else:
            continue
        fout = os.path.abspath("{}/{}".format(out_folder, (os.path.split(fname_in)[-1]).replace("RAW", "CORR")))
        inp.append((fname_in, fout, i))
    first = False
    p = partial(characterize_module, IL_MODE, max_cells,
               (thresholds_offset_hard, thresholds_offset_sigma,
                thresholds_noise_hard, thresholds_noise_sigma), rawversion, loc, acq_rate)
    results = list(map(p, inp))
    #results = view.map_sync(p, inp)
    for ii, r in enumerate(results):
        i = modules[ii]
        offset, noise, gain, bp, thiscell, thisacq = r
        all_cells.append(thiscell)
        all_acq_rate.append(thisacq)
        qm = "Q{}M{}".format(i//4 +1, i % 4 + 1)
        if qm not in offset_g:
            offset_g[qm] = np.zeros((offset.shape[0], offset.shape[1], offset.shape[2], 3))
            noise_g[qm] = np.zeros_like(offset_g[qm])
            gain_g[qm] = np.zeros_like(offset_g[qm])
            badpix_g[qm] = np.zeros_like(offset_g[qm], np.uint32)
        
        offset_g[qm][...,gg] = offset
        noise_g[qm][...,gg] = noise
        gain_g[qm][...,gg] = gain
        badpix_g[qm][...,gg] = bp
    gg +=1

duration = (datetime.now()-start).total_seconds()
logger.runtime_summary_entry(success=True, runtime=duration,
                                   total_sequences=total_sequences,
                                   filesize=total_file_size)
logger.send()
max_cells = np.max(all_cells)
print("Using {} memory cells".format(max_cells))
acq_rate = np.max(all_acq_rate)
print("Using {} MHz acquisition rate".format(acq_rate))

The thresholds for gain switching are then defined as the mean value between in individual gain bit levels. Note that these thresholds need to be refined with charge induced thresholds, as the two are not the same.

In [ ]:
thresholds_g = {}
for qm in gain_g.keys():
    thresholds_g[qm] = np.zeros((gain_g[qm].shape[0], gain_g[qm].shape[1], gain_g[qm].shape[2], 5))
    thresholds_g[qm][...,0] = (gain_g[qm][...,1]+gain_g[qm][...,0])/2
    thresholds_g[qm][...,1] = (gain_g[qm][...,2]+gain_g[qm][...,1])/2
    for i in range(3):
        thresholds_g[qm][...,2+i] = gain_g[qm][...,i]

In [ ]:
res = OrderedDict()
for i in modules:
    qm = "Q{}M{}".format(i//4+1, i%4+1)
    res[qm] = {'Offset': offset_g[qm],
               'Noise': noise_g[qm],
               'ThresholdsDark': thresholds_g[qm],
               'BadPixelsDark': badpix_g[qm]    
               }
    
if local_output:
    for qm in offset_g.keys():
        ofile = "{}/agipd_offset_store_{}_{}.h5".format(out_folder, "_".join(offset_runs.values()), qm)
        store_file = h5py.File(ofile, "w")
        store_file["{}/Offset/0/data".format(qm)] = offset_g[qm]
        store_file["{}/Noise/0/data".format(qm)] = noise_g[qm]
        store_file["{}/Threshold/0/data".format(qm)] = thresholds_g[qm]
        store_file["{}/BadPixels/0/data".format(qm)] = badpix_g[qm]
        store_file.close()

In [ ]:
# Retrieve existing constants for comparison
clist = ["Offset", "Noise", "BadPixelsDark"]
old_const = {}
old_mdata = {}
detinst = getattr(Detectors, dinstance)

print('Retrieve pre-existing constants for comparison.')

for qm in res:
    for const in res[qm]:
        metadata = ConstantMetaData()
        dconst = getattr(Constants.AGIPD, const)()
        dconst.data = res[qm][const]
        metadata.calibration_constant = dconst

        # Setting conditions
        condition = Conditions.Dark.AGIPD(memory_cells=max_cells,
                                          bias_voltage=bias_voltage,
                                          acquisition_rate=acq_rate,
                                          gain_setting=gain_setting)
        device = getattr(detinst, qm)
        data, mdata = get_from_db(device,
                                  getattr(Constants.AGIPD, const)(),
                                  condition,
                                  None,
                                  cal_db_interface, creation_time=creation_time,
                                  verbosity=2, timeout=cal_db_timeout)

        old_const[const] = data

        if mdata is not None and data is not None:
            time = mdata.calibration_constant_version.begin_at
            old_mdata[const] = time.isoformat()
            os.makedirs('{}/old/'.format(out_folder), exist_ok=True)
            save_const_to_h5(mdata, '{}/old/'.format(out_folder))
        else:
            old_mdata[const] = "Not found"

In [ ]:
proposal = list(filter(None, in_folder.strip('/').split('/')))[-2]
file_loc = 'proposal:{} runs:{} {} {}'.format(proposal, run_low, run_med, run_high)

In [ ]:
for qm in res:
    for const in res[qm]:
        metadata = ConstantMetaData()
        dconst = getattr(Constants.AGIPD, const)()
        dconst.data = res[qm][const]
        metadata.calibration_constant = dconst

        # set the operating condition
        condition = Conditions.Dark.AGIPD(memory_cells=max_cells,
                                          bias_voltage=bias_voltage,
                                          acquisition_rate=acq_rate,
                                          gain_setting=gain_setting)
        detinst = getattr(Detectors, dinstance)
        device = getattr(detinst, qm)
        
        metadata.detector_condition = condition

        # specify the a version for this constant
        if creation_time is None:
            metadata.calibration_constant_version = Versions.Now(device=device)
        else:
            metadata.calibration_constant_version = Versions.Timespan(device=device,
                                                                      start=creation_time)

        metadata.calibration_constant_version.raw_data_location = file_loc

        if db_output:
            try:
                metadata.send(cal_db_interface, timeout=cal_db_timeout)
                msg = 'Const {} for module {} was injected to the calibration DB. Begin at: {}'
                print(msg.format(const, qm,
                                 metadata.calibration_constant_version.begin_at))
            except Exception as e:
                print(e)

        if local_output:
            save_const_to_h5(metadata, out_folder)
            print("Calibration constant {} is stored locally.".format(const))


In [ ]:
qm = "Q{}M{}".format(modules[0]//4+1, modules[0] % 4+1)
display(Markdown('## Position of the module {}, it tiles and ASICs of tile ##'.format(qm)))

fig, ax = plt.subplots(1, figsize=(10, 10))
ax.set_axis_off()

ax.set_xlim(0, 97)
ax.set_ylim(0, 100)

q_poses = np.array([[51, 47], [47, 1], [1, 5], [5, 51]])
m_poses = np.array([[22.5, 20.5], [22.5, 0.5], [0.5, 0.5], [0.5, 20.5]])

for iq, q_pos in enumerate(q_poses):
    ax.add_patch(matplotlib.patches.Rectangle(q_pos, 45, 45, linewidth=2, edgecolor='k',
                                   facecolor='mediumblue', fill=True))

    ax.text(q_pos[0]+20, q_pos[1]+41.5, 'Q{}'.format(iq+1), fontsize=22, color="white")
    for im, m_pos in enumerate(m_poses):
        ax.add_patch(matplotlib.patches.Rectangle(q_pos+m_pos, 22, 20, linewidth=3, edgecolor='k',
                                       facecolor='sandybrown', fill=True))

        if iq*4+im == modules[0]:
            for a_posx in range(2):
                for a_posy in range(8):
                    a_pos = np.array([a_posx*11., a_posy*20/8.])
                    pos = q_pos+m_pos+a_pos
        # Change Text for current processed module.
            pos = q_pos+m_pos+np.array([2.5, 8])
            ax.text(pos[0], pos[1], 'Q{}M{}'.format(
                iq+1, im+1),  fontsize=28, color='red')
        else:
            pos = q_pos+m_pos+np.array([5, 8])
            ax.text(pos[0], pos[1], 'Q{}M{}'.format(
                iq+1, im+1),  fontsize=22, color='k')

ax.add_patch(matplotlib.patches.Rectangle([65, 93], 50, 4, linewidth=1, edgecolor='black',
                                facecolor='mediumblue', fill=True))

ax.text(46, 98, 'ASICs:',  fontsize=22, color='black')

for i_pos in range(8):
    pos = np.array([65, 93]) + np.array([i_pos*50/8.+0.3, 0.3])

    ax.add_patch(matplotlib.patches.Rectangle(pos, 45/8., 3.4, linewidth=1, edgecolor='black',
                                   facecolor='sandybrown', fill=True))

    ax.text(pos[0]+0.5, pos[1]+0.5, '{}'.format(16-i_pos),
            fontsize=18, color='black')
    
ax.add_patch(matplotlib.patches.Rectangle([65, 98], 50, 4, linewidth=1, edgecolor='black',
                               facecolor='mediumblue', fill=True))
for i_pos in range(8):
    pos = np.array([65, 98]) + np.array([i_pos*50/8.+0.3, 0.3])

    ax.add_patch(matplotlib.patches.Rectangle(pos, 45/8., 3.4, linewidth=1, edgecolor='black',
                                   facecolor='sandybrown', fill=True))

    ax.text(pos[0]+1.5, pos[1]+0.5, '{}'.format(8-i_pos),
            fontsize=18, color='black')

## Single-Cell Overviews ##

Single cell overviews allow to identify potential effects on all memory cells, e.g. on sensor level. Additionally, they should serve as a first sanity check on expected behaviour, e.g. if structuring on the ASIC level is visible in the offsets, but otherwise no immediate artifacts are visible.

### High Gain ###

In [ ]:
cell = 3
gain = 0
out_folder = None
show_overview(res, cell, gain, out_folder=out_folder, infix="_".join(offset_runs.values()))

### Medium Gain ###

In [ ]:
cell = 3
gain = 1
show_overview(res, cell, gain, out_folder=out_folder, infix="_".join(offset_runs.values()))

### Low Gain ###

In [ ]:
cell = 3
gain = 2
show_overview(res, cell, gain, out_folder=out_folder, infix="_".join(offset_runs.values()))

## Global Bad Pixel Behaviour ##

The following plots show the results of bad pixel evaluation for all evaluated memory cells. Cells are stacked in the Z-dimension, while pixels values in x/y are rebinned with a factor of 2. This excludes single bad pixels present only in disconnected pixels. Hence, any bad pixels spanning at least 4 pixels in the x/y-plane, or across at least two memory cells are indicated. Colors encode the bad pixel type, or mixed type.

### High Gain ###

In [ ]:
cols = {BadPixels.NOISE_OUT_OF_THRESHOLD.value: (BadPixels.NOISE_OUT_OF_THRESHOLD.name, '#FF000080'),
        BadPixels.OFFSET_NOISE_EVAL_ERROR.value: (BadPixels.OFFSET_NOISE_EVAL_ERROR.name, '#0000FF80'),
        BadPixels.OFFSET_OUT_OF_THRESHOLD.value: (BadPixels.OFFSET_OUT_OF_THRESHOLD.name, '#00FF0080'),
        BadPixels.OFFSET_OUT_OF_THRESHOLD.value | BadPixels.NOISE_OUT_OF_THRESHOLD.value: ('MIXED', '#DD00DD80')}

rebin = 8 if not high_res_badpix_3d else 2

gain = 0
for mod, data in badpix_g.items():
    plot_badpix_3d(data[...,gain], cols, title=mod, rebin_fac=rebin)

### Medium Gain ###

In [ ]:
gain = 1
for mod, data in badpix_g.items():
    plot_badpix_3d(data[...,gain], cols, title=mod, rebin_fac=rebin)

### Low Gain ###

In [ ]:
gain = 2
for mod, data in badpix_g.items():
    plot_badpix_3d(data[...,gain], cols, title=mod, rebin_fac=rebin)

## Aggregate values, and per Cell behaviour ##

The following tables and plots give an overview of statistical aggregates for each constant, as well as per cell behavior.

In [ ]:
create_constant_overview(offset_g, "Offset (ADU)", max_cells, 4000, 10000,
                         out_folder=out_folder, infix="_".join(offset_runs.values()))

In [ ]:
create_constant_overview(noise_g, "Noise (ADU)", max_cells, 0, 100,
                         out_folder=out_folder, infix="_".join(offset_runs.values()))

In [ ]:
create_constant_overview(thresholds_g, "Threshold (ADU)", max_cells, 4000, 10000, 3,
                         out_folder=out_folder, infix="_".join(offset_runs.values()))

In [ ]:
bad_pixel_aggregate_g = OrderedDict()
for m, d in badpix_g.items():
    bad_pixel_aggregate_g[m] = d.astype(np.bool).astype(np.float)
create_constant_overview(bad_pixel_aggregate_g, "Bad pixel fraction", max_cells, 0, 0.10, 3,
                         out_folder=out_folder, infix="_".join(offset_runs.values()))

## Summary tables ##

The following tables show summary information for the evaluated module. Values for currently evaluated constants are compared with values for pre-existing constants retrieved from the calibration database.

In [ ]:
table = []
gain_names = ['High', 'Medium', 'Low']
for qm in badpix_g.keys():
    for gain in range(3):

        l_data = []
        l_data_old = []

        data = np.copy(badpix_g[qm][:,:,:,gain])
        datau32 = data.astype(np.uint32)
        l_data.append(data)
        l_data.append(datau32 - np.bitwise_or(datau32,BadPixels.NOISE_OUT_OF_THRESHOLD.value))
        l_data.append(datau32 - np.bitwise_or(datau32,BadPixels.OFFSET_OUT_OF_THRESHOLD.value))
        l_data.append(datau32 - np.bitwise_or(datau32,BadPixels.OFFSET_NOISE_EVAL_ERROR.value))

        if old_const['BadPixelsDark'] is not None:
            dataold = np.copy(old_const['BadPixelsDark'][:, :, :, gain])
            datau32old = dataold.astype(np.uint32)
            l_data_old.append(dataold)
            l_data_old.append(datau32old - np.bitwise_or(datau32old,BadPixels.NOISE_OUT_OF_THRESHOLD.value))
            l_data_old.append(datau32old - np.bitwise_or(datau32old,BadPixels.OFFSET_OUT_OF_THRESHOLD.value))
            l_data_old.append(datau32old - np.bitwise_or(datau32old,BadPixels.OFFSET_NOISE_EVAL_ERROR.value))

        l_data_name = ['All bad pixels', 'NOISE_OUT_OF_THRESHOLD', 
                       'OFFSET_OUT_OF_THRESHOLD', 'OFFSET_NOISE_EVAL_ERROR']

        l_threshold = ['', '{}'.format(thresholds_noise_sigma), '{}'.format(thresholds_offset_sigma),
                      '{}/{}'.format(thresholds_offset_hard, thresholds_noise_hard)]

        for i in range(len(l_data)):
            line = ['{}, gain {}'.format(l_data_name[i], gain_names[gain]),
                      l_threshold[i],
                      len(l_data[i][l_data[i]>0].flatten())
                   ]

            if old_const['BadPixelsDark'] is not None:
                line += [len(l_data_old[i][l_data_old[i]>0].flatten())]
            else:
                line += ['-']

        table.append(line)

display(Markdown('### Number of bad pixels ###'.format(qm)))
if len(table)>0:
    md = display(Latex(tabulate.tabulate(table, tablefmt='latex', 
                                     headers=["Pixel type", "Threshold", "New constant", "Old constant "])))  

In [ ]:

header = ['Parameter', 
          "New constant", "Old constant ", 
          "New constant", "Old constant ", 
          "New constant", "Old constant "]

for const in ['Offset', 'Noise']:
    table = [['','High gain', 'High gain', 'Medium gain', 'Medium gain', 'Low gain', 'Low gain']]
    for qm in res.keys():

        data = np.copy(res[qm][const])
        data[res[qm]['BadPixelsDark']>0] = np.nan

        if old_const[const] is not None and old_const['BadPixelsDark'] is not None :
            dataold = np.copy(old_const[const])
            dataold[old_const['BadPixelsDark']>0] = np.nan

        f_list = [np.nanmedian, np.nanmean, np.nanstd, np.nanmin, np.nanmax]
        n_list = ['Median', 'Mean', 'Std', 'Min', 'Max']

        for i, f in enumerate(f_list):
            line = [n_list[i]]
            for gain in range(3):
                line.append('{:6.1f}'.format(f(data[...,gain])))
                if old_const[const] is not None and old_const['BadPixelsDark'] is not None:
                    line.append('{:6.1f}'.format(f(dataold[...,gain])))
                else:
                    line.append('-')

            table.append(line)

    display(Markdown('### {} [ADU], good pixels only ###'.format(const)))
    md = display(Latex(tabulate.tabulate(table, tablefmt='latex', headers=header)))  